In [23]:
import numpy as np
import pandas as pd
import csv
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import ParameterGrid
from sklearn.metrics import classification_report
from nltk.tokenize import TweetTokenizer

In [2]:
def compute_accuracy(predictions, actual):
    p = predictions
    a = actual
    if type(p) is not np.ndarray:
        p = p.to_numpy()
    if type(a) is not np.ndarray:
        a = a.to_numpy()
    correct = 0
    for i in range(len(a)):
        if p[i] == a[i]:
            correct += 1
    return correct / len(a) * 100

COUNTVECTORIZER

In [3]:
# load data
sentiments = pd.read_csv('train.csv', quoting=csv.QUOTE_ALL, encoding="utf-8", index_col=0)

X = sentiments["Text"]
y = sentiments["IsPositive"]

# split data for training and validation sets
X_train, X_validation, y_train, y_validation = train_test_split(X, y, test_size=0.25, random_state=42)

In [4]:
# set up custom stop words
# sources:
# tagalog - https://github.com/explosion/spaCy/discussions/6122
# english - https://gist.githubusercontent.com/ZohebAbai/513218c3468130eacff6481f424e4e64/raw/b70776f341a148293ff277afa0d0302c8c38f7e2/gist_stopwords.txt
# punctuations - ourselves
gist_file = open("gist_stopwords.txt", "r")
try:
    content = gist_file.read()
    stopwords = content.split(",")
finally:
    gist_file.close()
tagalog = ['ba',
 'eh',
 'kasi',
 'lang',
 'mo',
 'naman',
 'opo',
 'po',
 'si',
 'talaga',
 'yung',
]
punctuations = ['!', '.', ',', '\"', '\'', ';', ':', '?', '*', '%', '@', '&', '$', '^', '(', ')', '_', '-', '+', '=']
stopwords += tagalog
stopwords += punctuations

In [8]:
# initialize countvectorizer and multinomial naive bayes for tuning
count_vect = CountVectorizer()
sentiment_nb = MultinomialNB()
tk = TweetTokenizer()

# set up hyperparameters
NB_hyperparameters = [{
    'alpha': [0.1,0.5,1,3,5],
    'fit_prior': [True, False]
}]

CV_hyperparameters = [{
    'stop_words' : [stopwords, 'english'],
    'ngram_range' : [(1,1), (1,2), (2,2)],
    'max_df' : [0.5, 0.9, 1.0],
    'min_df' : [1, 100, 1000],
    'token_pattern' : [r'[^\s]+', r'(?u)\b\w\w+\b'],
    'tokenizer' : [tk, None]
}]

In [9]:
# tuning
best_score = 0
for g in ParameterGrid(NB_hyperparameters):

    sentiment_nb.set_params(**g)
    for h in ParameterGrid(CV_hyperparameters):
        print(g)
        print(h)
        
        try:
            count_vect.set_params(**h)
            count_vect.fit(X_train)
        except:
            print('After pruning, no terms remain. Try a lower min_df or a higher max_df.')
            continue
        
        X_train_count_sparse_matrix = count_vect.transform(X_train)
        X_validation_count_sparse_matrix = count_vect.transform(X_validation)
        
        sentiment_nb.fit(X_train_count_sparse_matrix, y_train)
        predictions = sentiment_nb.predict(X_train_count_sparse_matrix)
        train_acc = compute_accuracy(predictions, y_train)

        predictions = sentiment_nb.predict(X_validation_count_sparse_matrix)
        val_acc = compute_accuracy(predictions, y_validation)

        print(f"Train acc: {train_acc}% \t Val acc: {val_acc}%", end="\n\n")

        if val_acc > best_score:
            best_score = val_acc
            best_NB= g
            best_CV = h
            

print("Best accuracy: ", best_score, "%")
print("Best hyperparameters in NB: ", best_NB)
print("Best hyperparameters in CV: ", best_CV)

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'apparently', 'appear', 'appreciate', 'appropriate', 'approximately', 'ar', 'are', 'aren', 'arent', "aren't", 'arise', 'around', 'as', "a's", 'aside', 'ask', 'asking', 'associated', 'at', 'au', 'auth', 'av', 'available', 'aw', 'away', 'awfully', 'ax', 'ay', 'az', 

Train acc: 99.06782223118009% 	 Val acc: 88.41357418184566%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 1), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 98.64582283583594% 	 Val acc: 88.02433678482352%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'ap

Train acc: 99.87780913030335% 	 Val acc: 87.23452497921548%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 99.7959286506097% 	 Val acc: 86.36157508880659%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (2, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'app

Train acc: 99.27819207900836% 	 Val acc: 69.91157130980274%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (2, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 99.36385165776478% 	 Val acc: 72.31123875746354%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 100, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', '

Train acc: 83.34425073062583% 	 Val acc: 83.59912327110574%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 100, 'ngram_range': (1, 1), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 83.74735463065606% 	 Val acc: 83.77673645227118%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 100, 'ngram_range': (1, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart',

...

Train acc: 83.05829890154187% 	 Val acc: 83.0662837276094%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 100, 'ngram_range': (1, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 83.00791091403809% 	 Val acc: 82.90378656186229%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 100, 'ngram_range': (2, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'a

Train acc: 56.80237831301018% 	 Val acc: 56.779532915123575%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 100, 'ngram_range': (2, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 57.623702509321774% 	 Val acc: 57.65626180938705%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart'

Train acc: 73.90406127179281% 	 Val acc: 74.14405562693675%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 1), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 74.13710571399778% 	 Val acc: 74.53707202781347%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart',

Train acc: 73.71006751990325% 	 Val acc: 73.79260826846044%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 73.91917766804393% 	 Val acc: 74.29899478497468%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (2, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart',

Train acc: 51.379371157915955% 	 Val acc: 51.556949588088585%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (2, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 51.5506903154288% 	 Val acc: 51.651424684453175%

Best accuracy:  88.98042476003324 %
Best hyperparameters in NB:  {'alpha': 1, 'fit_prior': False}
Best hyperparameters in CV:  {'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'an

In [11]:
# use the best parameters that we got from tuning
# best count vectorizer parameters: max_df=0.5, min_df=1, ngram_range=(1,1), stop_words=stopwords, token_pattern='[^\\s]+'
# best NB parameters: alpha=1, fit_prior=False
count_vect = CountVectorizer(max_df=0.5, min_df=1, ngram_range=(1,1), stop_words=stopwords, token_pattern='[^\\s]+')
sentiment_nb = MultinomialNB(alpha=1, fit_prior=False)
count_vect.fit(X_train)
X_train_val_count_sparse_matrix = count_vect.transform(X)
sentiment_nb.fit(X_train_val_count_sparse_matrix, y)

MultinomialNB(alpha=1, fit_prior=False)

In [17]:
predictions = sentiment_nb.predict(X_train_val_count_sparse_matrix)
print("Count Vectorizer, Naive Bayes")
print(classification_report(y, predictions, digits=4))

Count Vectorizer, Naive Bayes
              precision    recall  f1-score   support

       False     0.9362    0.9625    0.9492     52923
        True     0.9614    0.9344    0.9477     52923

    accuracy                         0.9485    105846
   macro avg     0.9488    0.9485    0.9485    105846
weighted avg     0.9488    0.9485    0.9485    105846



In [18]:
# load the test dataset
sentiments = pd.read_csv('test.csv', quoting=csv.QUOTE_ALL, encoding="utf-8")

X_test = sentiments["Text"]

X_test_val_count_sparse_matrix = count_vect.transform(X_test)

# predict values of test dataset
predictions = sentiment_nb.predict(X_test_val_count_sparse_matrix)
# print(predictions)

In [20]:
pred = []
ids = sentiments['DocumentId'].tolist()
header = ['DocumentId', 'IsPositive']
for i in range(len(predictions)):
    pred.append({'DocumentId': str(ids[i]),
                'IsPositive' : str(predictions[i])})
# print(pred)
df = pd.DataFrame(pred, columns=['DocumentId', 'IsPositive'])
df.to_csv('submission.csv', quoting=csv.QUOTE_ALL, index=False)

TFIDFVectorizer

In [21]:
# load data
sentiments = pd.read_csv('train.csv', quoting=csv.QUOTE_ALL, encoding="utf-8", index_col=0)

X = sentiments["Text"]
y = sentiments["IsPositive"]

# split data for training and validation sets
X_train, X_validation, y_train, y_validation = train_test_split(X, y, test_size=0.25, random_state=42)

In [25]:
# initialize countvectorizer and multinomial naive bayes for tuning
tfidf_vect = TfidfVectorizer()
sentiment_nb = MultinomialNB()


# set up hyperparameters
NB_hyperparameters = [{
    'alpha': [0.1,0.5,1,3,5],
    'fit_prior': [True, False]
}]

TFIDF_hyperparameters = [{
    'stop_words' : [stopwords, 'english'],
    'ngram_range' : [(1,1), (1,2), (2,2)],
    'max_df' : [0.5, 0.9, 1.0],
    'min_df' : [1, 100, 1000],
    'token_pattern' : [r'[^\s]+', r'(?u)\b\w\w+\b'],
    'tokenizer' : [tk, None]
}]

In [26]:
# tuning
best_score = 0
for g in ParameterGrid(NB_hyperparameters):

    sentiment_nb.set_params(**g)
    for h in ParameterGrid(TFIDF_hyperparameters):
        print(g)
        print(h)
        
        try:
            tfidf_vect.set_params(**h)
            tfidf_vect.fit(X_train)
        except:
            print('After pruning, no terms remain. Try a lower min_df or a higher max_df.')
            continue
        
        X_train_count_sparse_matrix = tfidf_vect.transform(X_train)
        X_validation_count_sparse_matrix = tfidf_vect.transform(X_validation)
        
        sentiment_nb.fit(X_train_count_sparse_matrix, y_train)
        predictions = sentiment_nb.predict(X_train_count_sparse_matrix)
        train_acc = compute_accuracy(predictions, y_train)

        predictions = sentiment_nb.predict(X_validation_count_sparse_matrix)
        val_acc = compute_accuracy(predictions, y_validation)

        print(f"Train acc: {train_acc}% \t Val acc: {val_acc}%", end="\n\n")

        if val_acc > best_score:
            best_score = val_acc
            best_NB= g
            best_TFIDF = h
            

print("Best accuracy: ", best_score, "%")
print("Best hyperparameters in NB: ", best_NB)
print("Best hyperparameters in TFIDF: ", best_TFIDF)

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'apparently', 'appear', 'appreciate', 'appropriate', 'approximately', 'ar', 'are', 'aren', 'arent', "aren't", 'arise', 'around', 'as', "a's", 'aside', 'ask', 'asking', 'associated', 'at', 'au', 'auth', 'av', 'available', 'aw', 'away', 'awfully', 'ax', 'ay', 'az', 

Train acc: 99.07034163055528% 	 Val acc: 86.86418260146625%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 1), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 98.82973899022474% 	 Val acc: 86.72435945884665%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'ap

Train acc: 99.91182102186839% 	 Val acc: 86.39558612349785%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 99.82490174342436% 	 Val acc: 85.49996220996145%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (2, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'ap

Train acc: 99.31346367026102% 	 Val acc: 69.990930390749%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 1, 'ngram_range': (2, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 99.4293560415197% 	 Val acc: 72.31123875746354%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 100, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 'app

Train acc: 83.19938526655245% 	 Val acc: 83.34593001284861%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 100, 'ngram_range': (1, 1), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 83.62390406127179% 	 Val acc: 83.49331116317738%

{'alpha': 0.1, 'fit_prior': True}
{'max_df': 0.5, 'min_df': 100, 'ngram_range': (1, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart',

...

Train acc: 83.13388088279754% 	 Val acc: 83.29302395888443%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 100, 'ngram_range': (1, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 83.05074070341631% 	 Val acc: 82.86977552717104%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 100, 'ngram_range': (2, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', '

Train acc: 56.852766300513956% 	 Val acc: 56.862670999924426%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 100, 'ngram_range': (2, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 57.680388995263534% 	 Val acc: 57.720504874914965%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apar

Train acc: 73.62188854177164% 	 Val acc: 73.76993424533293%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 1), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 73.79824649803487% 	 Val acc: 73.99289547275339%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart',

Train acc: 73.57276025395547% 	 Val acc: 73.7774922530421%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (1, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 73.65212133427391% 	 Val acc: 73.88330436097044%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (2, 2), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 'anyhow', 'anymore', 'anyone', 'anything', 'anyway', 'anyways', 'anywhere', 'ao', 'ap', 'apart', 

Train acc: 50.5945782525446% 	 Val acc: 50.680220693825106%

{'alpha': 5, 'fit_prior': False}
{'max_df': 1.0, 'min_df': 1000, 'ngram_range': (2, 2), 'stop_words': 'english', 'token_pattern': '[^\\s]+'}
Train acc: 51.548170916053614% 	 Val acc: 51.651424684453175%

Best accuracy:  88.11125387347896 %
Best hyperparameters in NB:  {'alpha': 1, 'fit_prior': False}
Best hyperparameters in TFIDF:  {'max_df': 0.5, 'min_df': 1, 'ngram_range': (1, 1), 'stop_words': ['0o', '0s', '3a', '3b', '3d', '6b', '6o', 'a', 'a1', 'a2', 'a3', 'a4', 'ab', 'able', 'about', 'above', 'abst', 'ac', 'accordance', 'according', 'accordingly', 'across', 'act', 'actually', 'ad', 'added', 'adj', 'ae', 'af', 'affected', 'affecting', 'affects', 'after', 'afterwards', 'ag', 'again', 'against', 'ah', 'ain', "ain't", 'aj', 'al', 'all', 'allow', 'allows', 'almost', 'alone', 'along', 'already', 'also', 'although', 'always', 'am', 'among', 'amongst', 'amoungst', 'amount', 'an', 'and', 'announce', 'another', 'any', 'anybody', 

In [27]:
# use the best parameters that we got from tuning
# best TFIDF vectorizer parameters: max_df=1.0, min_df=1000, ngram_range=(1,2), stop_words=stopwords, token_pattern='[^\\s]+'
# best NB parameters: alpha=1, fit_prior=False
tfidf_vect = TfidfVectorizer(max_df=1.0, min_df=1000, ngram_range=(1,2), stop_words=stopwords, token_pattern='[^\\s]+')
sentiment_nb = MultinomialNB(alpha=1, fit_prior=False)
tfidf_vect.fit(X_train)
X_train_val_count_sparse_matrix = tfidf_vect.transform(X)
sentiment_nb.fit(X_train_val_count_sparse_matrix, y)

MultinomialNB(alpha=1, fit_prior=False)

In [28]:
predictions = sentiment_nb.predict(X_train_val_count_sparse_matrix)
print("TFIDF Vectorizer, Naive Bayes")
print(classification_report(y, predictions, digits=4))

TFIDF Vectorizer, Naive Bayes
              precision    recall  f1-score   support

       False     0.7078    0.8043    0.7530     52923
        True     0.7734    0.6680    0.7169     52923

    accuracy                         0.7362    105846
   macro avg     0.7406    0.7362    0.7349    105846
weighted avg     0.7406    0.7362    0.7349    105846



In [30]:
# load the test dataset
sentiments = pd.read_csv('test.csv', quoting=csv.QUOTE_ALL, encoding="utf-8")

X_test = sentiments["Text"]

X_test_val_count_sparse_matrix = tfidf_vect.transform(X_test)

# predict values of test dataset
predictions = sentiment_nb.predict(X_test_val_count_sparse_matrix)
# print(predictions)

In [31]:
pred = []
ids = sentiments['DocumentId'].tolist()
header = ['DocumentId', 'IsPositive']
for i in range(len(predictions)):
    pred.append({'DocumentId': str(ids[i]),
                'IsPositive' : str(predictions[i])})
# print(pred)
df = pd.DataFrame(pred, columns=['DocumentId', 'IsPositive'])
df.to_csv('submission.csv', quoting=csv.QUOTE_ALL, index=False)